## NDCG Score

In [1]:
import numpy as np
import pandas as pd
import json 

In [2]:
# import utility functions 
from ret import read_data # utility func to load data
from ret import get_id_from_info # utility func to return id by entering song's info
from ret import display_res # utility func to display results 
from ret import get_genre #utility func to get the genres from a list of id´s
from ret import get_genre_from_query #utility func to get the id and genre from the query
from ret import get_genre_from_ids #utility func to get the id and genre from the retrieved results
from ret import generate_cos_sim_matrix

# import the retrieval systems 
from ret import random_baseline # baseline retrieval system that returns random results 
from ret import text_based # modularized text based retrieval system
from ret import audio_based # modularized audio based retrieval system
from ret import video_based # modularized video based retrieval system

# import wrapper function to calculate cosine similarity
from ret import cos_sim 

# import evaluation functions 
from ret import gen_cov_10
# from ret import ndcg_score
from ret import gen_div_10
from ret import calculate_precision_at_k
from ret import calculate_recall_at_k
from ret import plot_precision_recall_curve
from ret import get_avg_recall_at_k
from ret import get_avg_precision_at_k

In [3]:
"""
Please put data files in ""./data/" before use 
"""

info = read_data("information")
genres = read_data("genres")

# text embeddings 
tfidf = read_data("lyrics_tf-idf")
word2vec = read_data("lyrics_word2vec")
bert = read_data("lyrics_bert")

# audio embeddings
blf_correlation = read_data("blf_correlation")
ivec256 = read_data("ivec256")
mfcc_stats = read_data("mfcc_stats")
musicnn = read_data("musicnn")

# video embeddings
vgg19 = read_data("vgg19")
# info

In [4]:
#preprocessing: Song does not exist in other datasets so it needs to be omitted from the info dataset
info_df = info[info['id'] != '03Oc9WeMEmyLLQbj']

In [5]:
all_genres = list(set([item for id in genres['id'] for item in get_genre(id, genres)]))

In [6]:
arr1 = np.array(["pop", "countrypop", "poprock"])
arr2 = np.array(["pop"])
len(np.intersect1d(arr1, arr2))

pd.set_option('max_colwidth', 400)

In [7]:
import ast
from functools import reduce

def ndcg_score(query_id, retrieved_ids, genres):
    # 1. convert all the values in column "genre" from str to nd.array
    genres["genre_arr"] = genres["genre"].apply(lambda x: np.array(ast.literal_eval(x)))
    
    # 2. calculate the rel for each track 
    query_genre = genres.loc[genres["id"] == query_id, 'genre_arr'].to_numpy()[0]
    retrieved_genre = pd.DataFrame(retrieved_ids, columns=['id'])
    retrieved_genre = pd.merge(genres, retrieved_genre, on="id", how="right")
    retrieved_genre["rel"] = retrieved_genre["genre_arr"].apply(lambda x: 2 * len(np.intersect1d(x, query_genre)) / (len(x) + len(query_genre)))
    
    # 3. calculate dcg
    rel = retrieved_genre["rel"].to_numpy()
    gain = np.empty(rel.shape)
    for i, _ in enumerate(rel):
        gain[...,i] = rel[...,i] / np.log2(i + 2)
    dcg = np.sum(gain)
    
    # 4. calculate idcg
    rel_sort = np.sort(rel)[::-1]
    rel_sort_gain = np.empty(rel_sort.shape)

    for i, _ in enumerate(rel_sort):
        if rel_sort_gain[...,i] != 0: 
            rel_sort_gain[...,i] = 1 / np.log2(i + 2)
    idcg = np.sum(rel_sort_gain)
    
    # 5. calculate ndcg
    ndcg = dcg / idcg
    print(f"ndcg{ndcg}")
    return ndcg 

In [8]:
def calc_ndcg10(df, genres, embedding):
    # Define the value of k
    k = 10

    # Generate the cosine similarity matrix
    cos_sim_matrix = generate_cos_sim_matrix(embedding)

    # Define an empty list to store the ndcg scores
    ndcg_scores = []

    # Loop over each query track
    for idx, query_id in enumerate(df.id):
        # Get the row index of the query track in the cosine similarity matrix
        query_index = cos_sim_matrix.index.get_loc(query_id)

        # Get the top-k most similar tracks using the cosine similarity matrix
        similar_tracks_indices = np.argsort(cos_sim_matrix.iloc[query_index])[::-1][1:k+1].index.values
        
        # Calculate ndcg score 
        ndcg = ndcg_score(query_id, similar_tracks_indices, genres)
    
        # Append the ndcg score to the list
        ndcg_scores.append(ndcg)

        # Print progress
        print(f'Processed row {idx+1}/{len(df)}')

    # Calculate the ndcg over all query tracks
    ndcg_scores = [0 if np.isnan(x) or np.isinf(x) else x for x in ndcg_scores]
    avg_ndcg = np.mean(ndcg_scores)

    # Print the result
    print(f'Average ndcg@{k}: {avg_ndcg:.9f}')

    return avg_ndcg

In [9]:
calc_ndcg10(info_df, genres, blf_correlation)

(1325, 10094)


/Users/tarkhon/Documents/jku_linz/WS2023:2024/kv_search_and_retrieval/project_3_team_E/ret.py:485: RuntimeWarning: invalid value encountered in true_divide
  cos_sim_matrix = np.triu(embedding_matrix.dot(embedding_transpose) / (np.linalg.norm(embedding_matrix, axis=1) * np.linalg.norm(embedding_matrix, axis=1)[:, None]))


ndcg0.20654799676191654
Processed row 1/10094
ndcg0.03639022898778738
Processed row 2/10094
ndcg0.20654799676191654
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.08799356866888737
Processed row 5/10094
ndcg0.20041283346356892
Processed row 6/10094
ndcg0.27956398269686233
Processed row 7/10094
ndcg0.02342428840590031
Processed row 8/10094
ndcg0.07202346408519873
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.08203491668318215
Processed row 11/10094
ndcg0.10881418735255498
Processed row 12/10094
ndcg0.16110803873658422
Processed row 13/10094
ndcg0.2212241635372666
Processed row 14/10094
ndcg0.022576170558260732
Processed row 15/10094
ndcg0.0712198886345532
Processed row 16/10094
ndcg0.18555211324477774
Processed row 17/10094
ndcg0.22763047388425528
Processed row 18/10094
ndcg0.26405578857211465
Processed row 19/10094
ndcg0.008586811607035068
Processed row 20/10094
ndcg0.08705610288820576
Processed row 21/10094
ndcg0.009063856696314794
Processed row 22/10094
ndcg0.

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.26070677812515075
Processed row 26/10094
ndcg0.061567649854120166
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.28548340900827784
Processed row 29/10094
ndcg0.0
Processed row 30/10094
ndcg0.33219008274336564
Processed row 31/10094
ndcg0.21129519989839937
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.23926359662345145
Processed row 37/10094
ndcg0.019783302398486996
Processed row 38/10094
ndcg0.26101085279292324
Processed row 39/10094
ndcg0.22967068200864912
Processed row 40/10094
ndcg0.22568257191896568
Processed row 41/10094
ndcg0.24093000256991845
Processed row 42/10094
ndcg0.34687984835347224
Processed row 43/10094
ndcg0.20330641365094054
Processed row 44/10094
ndcg0.33085111792979793
Processed row 45/10094
ndcg0.24562929634133054
Processed row 46/10094
ndcg0.13112413171511844
Processed row 47/10094
ndcg0.20654799676191654
Proce

...

ndcg0.22902078372355317
Processed row 9424/10094
ndcg0.007415882751530286
Processed row 9425/10094
ndcg0.11917229614020224
Processed row 9426/10094
ndcg0.11515099558896413
Processed row 9427/10094
ndcg0.23110612559676816
Processed row 9428/10094
ndcg0.17398396370738398
Processed row 9429/10094
ndcg0.2129819026917045
Processed row 9430/10094
ndcg0.2213550525419009
Processed row 9431/10094
ndcg0.09711503849071362
Processed row 9432/10094
ndcg0.008157471026683315
Processed row 9433/10094
ndcg0.2592182339402891
Processed row 9434/10094
ndcg0.10881418735255498
Processed row 9435/10094
ndcg0.12393819216262426
Processed row 9436/10094
ndcg0.28998732680923645
Processed row 9437/10094
ndcg0.2638229411149302
Processed row 9438/10094
ndcg0.295009805984265
Processed row 9439/10094
ndcg0.15528334486923864
Processed row 9440/10094
ndcg0.20868303320771095
Processed row 9441/10094
ndcg0.0
Processed row 9442/10094
ndcg0.10311586529117941
Processed row 9443/10094
ndcg0.13292576912913687
Processed row 94

ndcg0.11882289479673357
Processed row 9600/10094
ndcg0.0
Processed row 9601/10094
ndcg0.024307568576274013
Processed row 9602/10094
ndcg0.0
Processed row 9603/10094
ndcg0.04366827478534486
Processed row 9604/10094
ndcg0.0
Processed row 9605/10094
ndcg0.23302702445050685
Processed row 9606/10094
ndcg0.13208547692858513
Processed row 9607/10094
ndcg0.3363243984395322
Processed row 9608/10094
ndcg0.05566336101830281
Processed row 9609/10094
ndcg0.21832975058410684
Processed row 9610/10094
ndcg0.12393819216262426
Processed row 9611/10094
ndcg0.41812244424800715
Processed row 9612/10094
ndcg0.2573104326487848
Processed row 9613/10094
ndcg0.0
Processed row 9614/10094
ndcg0.0
Processed row 9615/10094
ndcg0.06467056416541112
Processed row 9616/10094
ndcg0.28748094914987116
Processed row 9617/10094
ndcg0.14269091981283794
Processed row 9618/10094
ndcg0.24675058762495541
Processed row 9619/10094
ndcg0.2270289852515088
Processed row 9620/10094
ndcg0.12393819216262426
Processed row 9621/10094
ndcg

ndcg0.33177007457531577
Processed row 9779/10094
ndcg0.22169771093880927
Processed row 9780/10094
ndcg0.23094414753611514
Processed row 9781/10094
ndcg0.2587087894125859
Processed row 9782/10094
ndcg0.20922987270092103
Processed row 9783/10094
ndcg0.0
Processed row 9784/10094
ndcg0.20316144085250326
Processed row 9785/10094
ndcg0.255394633466967
Processed row 9786/10094
ndcg0.3174721616162177
Processed row 9787/10094
ndcginf
Processed row 9788/10094
ndcg0.34132639568386736
Processed row 9789/10094
ndcg0.038681768656959374
Processed row 9790/10094
ndcg0.23302702445050685
Processed row 9791/10094
ndcg0.2587349747285567
Processed row 9792/10094
ndcg0.28525569781460364
Processed row 9793/10094
ndcg0.21727225606420147
Processed row 9794/10094
ndcg0.12801533003461726
Processed row 9795/10094
ndcg0.3011315039915555
Processed row 9796/10094
ndcg0.007093453066681143
Processed row 9797/10094
ndcg0.3480858077539051
Processed row 9798/10094
ndcg0.02426015265852492
Processed row 9799/10094
ndcg0.00

ndcg0.04544513004766614
Processed row 9955/10094
ndcg0.1150991451381296
Processed row 9956/10094
ndcg0.014360346803980361
Processed row 9957/10094
ndcg0.0
Processed row 9958/10094
ndcg0.14410305056272213
Processed row 9959/10094
ndcg0.21191194106346634
Processed row 9960/10094
ndcg0.1812143056855445
Processed row 9961/10094
ndcg0.1587350118104854
Processed row 9962/10094
ndcg0.0774181493833857
Processed row 9963/10094
ndcg0.30022851457481536
Processed row 9964/10094
ndcg0.07022881847379835
Processed row 9965/10094
ndcg0.0
Processed row 9966/10094
ndcg0.0
Processed row 9967/10094
ndcg0.07915160090801637
Processed row 9968/10094
ndcg0.14747526242926184
Processed row 9969/10094
ndcg0.095185492655657
Processed row 9970/10094
ndcg0.0
Processed row 9971/10094
ndcg0.23047361060616675
Processed row 9972/10094
ndcg0.12800710325603482
Processed row 9973/10094
ndcg0.013868559229288513
Processed row 9974/10094
ndcg0.0
Processed row 9975/10094
ndcg0.016186338326034815
Processed row 9976/10094
ndcg0

0.15040299801848814

In [10]:
calc_ndcg10(info_df, genres, mfcc_stats)

(103, 10094)
ndcg0.12846114094572664
Processed row 1/10094
ndcg0.031945968298148344
Processed row 2/10094
ndcg0.14405695336906407
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.137955167938515
Processed row 5/10094
ndcg0.22407079459204593
Processed row 6/10094
ndcg0.20307762208407198
Processed row 7/10094
ndcg0.03606748695964243
Processed row 8/10094
ndcg0.007741292242886216
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.09427934036394699
Processed row 11/10094
ndcg0.055679736728307665
Processed row 12/10094
ndcg0.16505452937903708
Processed row 13/10094
ndcg0.20492377255926775
Processed row 14/10094
ndcg0.07180403011899722
Processed row 15/10094
ndcg0.00847855817078014
Processed row 16/10094
ndcg0.174834139141679
Processed row 17/10094
ndcg0.30342731552321667
Processed row 18/10094
ndcg0.2763166662713605
Processed row 19/10094
ndcg0.04536824317332077
Processed row 20/10094
ndcg0.03384736300921198
Processed row 21/10094
ndcg0.12094377084782534
Processed row 22/10

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.19390737600259023
Processed row 26/10094
ndcg0.12577138970169977
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.32748711357715443
Processed row 29/10094
ndcg0.043816025621163365
Processed row 30/10094
ndcg0.31171621840144276
Processed row 31/10094
ndcg0.2615118196209538
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.28095440717275166
Processed row 37/10094
ndcg0.07153198716569978
Processed row 38/10094
ndcg0.17414453533185534
Processed row 39/10094
ndcg0.23276097816141617
Processed row 40/10094
ndcg0.2464281741790357
Processed row 41/10094
ndcg0.17543329962015364
Processed row 42/10094
ndcg0.3067466470578538
Processed row 43/10094
ndcg0.2289386152013084
Processed row 44/10094
ndcg0.3024989134266918
Processed row 45/10094
ndcg0.1694872812809495
Processed row 46/10094
ndcg0.07451711312887546
Processed row 47/10094
ndcg0.12846114094572

ndcg0.16385039271794488
Processed row 207/10094
ndcg0.20055517769157288
Processed row 208/10094
ndcg0.05941097515331771
Processed row 209/10094
ndcg0.26772836306108355
Processed row 210/10094
ndcg0.02719157008894438
Processed row 211/10094
ndcg0.2582352598468781
Processed row 212/10094
ndcg0.15221942777556058
Processed row 213/10094
ndcg0.04703368866304319
Processed row 214/10094
ndcg0.22769913468525407
Processed row 215/10094
ndcg0.1197762354587311
Processed row 216/10094
ndcg0.25144464160526014
Processed row 217/10094
ndcg0.26936650335778134
Processed row 218/10094
ndcg0.25618104347104864
Processed row 219/10094
ndcg0.027864551568577034
Processed row 220/10094
ndcg0.0
Processed row 221/10094
ndcg0.172231462456896
Processed row 222/10094
ndcg0.29714541873178846
Processed row 223/10094
ndcg0.13515223320273329
Processed row 224/10094
ndcg0.19999312811142642
Processed row 225/10094
ndcg0.13945167652474208
Processed row 226/10094
ndcg0.2187844274769058
Processed row 227/10094
ndcg0.213586

ndcg0.040787355133416574
Processed row 389/10094
ndcg0.14458856501304337
Processed row 390/10094
ndcg0.29714541873178846
Processed row 391/10094
ndcg0.13793958541907517
Processed row 392/10094
ndcg0.2597892704301763
Processed row 393/10094
ndcg0.0
Processed row 394/10094
ndcg0.0
Processed row 395/10094
ndcg0.13593805237155937
Processed row 396/10094
ndcg0.07434412830739676
Processed row 397/10094
ndcg0.02461320112605798
Processed row 398/10094
ndcg0.2788472462343586
Processed row 399/10094
ndcg0.14304021518882543
Processed row 400/10094
ndcg0.23928064143738456
Processed row 401/10094
ndcg0.00847855817078014
Processed row 402/10094
ndcg0.204789585772981
Processed row 403/10094
ndcg0.1313585073617247
Processed row 404/10094
ndcg0.21291075041787214
Processed row 405/10094
ndcg0.3041365552632712
Processed row 406/10094
ndcg0.15412429551706847
Processed row 407/10094
ndcg0.07557609975786439
Processed row 408/10094
ndcg0.1938459386088855
Processed row 409/10094
ndcg0.15144550007594254
Proces

...

ndcg0.3677213783952024
Processed row 9467/10094
ndcg0.17854674017929562
Processed row 9468/10094
ndcg0.0
Processed row 9469/10094
ndcg0.2642138816985908
Processed row 9470/10094
ndcg0.14224648861264405
Processed row 9471/10094
ndcg0.0
Processed row 9472/10094
ndcg0.0
Processed row 9473/10094
ndcg0.3517385036119983
Processed row 9474/10094
ndcg0.23928064143738456
Processed row 9475/10094
ndcg0.24435502922223312
Processed row 9476/10094
ndcg0.21751205795932296
Processed row 9477/10094
ndcg0.2034163307606262
Processed row 9478/10094
ndcg0.04031459028260845
Processed row 9479/10094
ndcg0.037626950930434555
Processed row 9480/10094
ndcg0.23928064143738456
Processed row 9481/10094
ndcg0.1313585073617247
Processed row 9482/10094
ndcg0.29714541873178846
Processed row 9483/10094
ndcg0.160397230157089
Processed row 9484/10094
ndcg0.0
Processed row 9485/10094
ndcg0.0
Processed row 9486/10094
ndcg0.21506143440574382
Processed row 9487/10094
ndcg0.2901612927641203
Processed row 9488/10094
ndcg0.265

ndcg0.2021453578210764
Processed row 9644/10094
ndcg0.023516844331521593
Processed row 9645/10094
ndcg0.0
Processed row 9646/10094
ndcg0.21476650832010838
Processed row 9647/10094
ndcg0.23422647690760331
Processed row 9648/10094
ndcg0.05596899356808677
Processed row 9649/10094
ndcg0.2304186318939034
Processed row 9650/10094
ndcg0.22522896489957198
Processed row 9651/10094
ndcg0.009371037978230681
Processed row 9652/10094
ndcg0.23087920340081625
Processed row 9653/10094
ndcg0.19916223487868
Processed row 9654/10094
ndcg0.0
Processed row 9655/10094
ndcg0.29714541873178846
Processed row 9656/10094
ndcg0.2710708475636809
Processed row 9657/10094
ndcg0.0
Processed row 9658/10094
ndcg0.15295943944838325
Processed row 9659/10094
ndcg0.2855767079249279
Processed row 9660/10094
ndcg0.06930441204567855
Processed row 9661/10094
ndcg0.035275266497282395
Processed row 9662/10094
ndcg0.0
Processed row 9663/10094
ndcg0.23884696451641185
Processed row 9664/10094
ndcg0.29901854725489857
Processed row 9

ndcg0.15966032533026916
Processed row 9819/10094
ndcg0.17564069966215468
Processed row 9820/10094
ndcg0.036766985414194986
Processed row 9821/10094
ndcg0.0
Processed row 9822/10094
ndcg0.25613303978847424
Processed row 9823/10094
ndcg0.2447626731668778
Processed row 9824/10094
ndcg0.1636089356460649
Processed row 9825/10094
ndcg0.19412821965354962
Processed row 9826/10094
ndcg0.20818194101471538
Processed row 9827/10094
ndcg0.3483837502041144
Processed row 9828/10094
ndcg0.19627345675361552
Processed row 9829/10094
ndcg0.2206309018321537
Processed row 9830/10094
ndcg0.04703368866304319
Processed row 9831/10094
ndcg0.26374137171997897
Processed row 9832/10094
ndcg0.11826535241272756
Processed row 9833/10094
ndcg0.19758421912244942
Processed row 9834/10094
ndcg0.0
Processed row 9835/10094
ndcg0.0
Processed row 9836/10094
ndcg0.14068656689244075
Processed row 9837/10094
ndcg0.0
Processed row 9838/10094
ndcg0.22679632172109132
Processed row 9839/10094
ndcg0.022338317250636112
Processed row

ndcg0.21881732244879432
Processed row 9994/10094
ndcg0.043816025621163365
Processed row 9995/10094
ndcg0.2036996989563046
Processed row 9996/10094
ndcg0.09406737732608637
Processed row 9997/10094
ndcg0.06454453913591517
Processed row 9998/10094
ndcg0.17743927861365355
Processed row 9999/10094
ndcg0.17751218520412285
Processed row 10000/10094
ndcg0.026166528280286396
Processed row 10001/10094
ndcg0.24779120154883
Processed row 10002/10094
ndcg0.23779581035310424
Processed row 10003/10094
ndcg0.12277027922665446
Processed row 10004/10094
ndcg0.32632089550651966
Processed row 10005/10094
ndcg0.2446308547782223
Processed row 10006/10094
ndcg0.3012057690200876
Processed row 10007/10094
ndcg0.09205465926225728
Processed row 10008/10094
ndcg0.00847855817078014
Processed row 10009/10094
ndcg0.28590081409190904
Processed row 10010/10094
ndcginf
Processed row 10011/10094
ndcg0.007121988863455319
Processed row 10012/10094
ndcg0.29714541873178846
Processed row 10013/10094
ndcg0.029705487576658855


0.1611674651497383

In [11]:
calc_ndcg10(info_df, genres, ivec256)

(99, 10094)
ndcg0.1635424840452836
Processed row 1/10094
ndcg0.045458692735805495
Processed row 2/10094
ndcg0.1635424840452836
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.1839690995946271
Processed row 5/10094
ndcg0.1481562567109056
Processed row 6/10094
ndcg0.1832778850368934
Processed row 7/10094
ndcg0.025099910851333278
Processed row 8/10094
ndcg0.03492695769272182
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.0
Processed row 11/10094
ndcg0.07601099933773522
Processed row 12/10094
ndcg0.10297918144396405
Processed row 13/10094
ndcg0.14002834743938275
Processed row 14/10094
ndcg0.022197940289582458
Processed row 15/10094
ndcg0.025084633953623037
Processed row 16/10094
ndcg0.11034413024596625
Processed row 17/10094
ndcg0.21700171514045774
Processed row 18/10094
ndcg0.1463543694021606
Processed row 19/10094
ndcg0.11699693204296412
Processed row 20/10094
ndcg0.03895598269844726
Processed row 21/10094
ndcg0.06750164279198555
Processed row 22/10094
ndcg0.2618601

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.08525921275341616
Processed row 26/10094
ndcg0.0437259453639426
Processed row 27/10094
ndcg0.02537418620368887
Processed row 28/10094
ndcg0.15146734739922887
Processed row 29/10094
ndcg0.0
Processed row 30/10094
ndcg0.21558658052946897
Processed row 31/10094
ndcg0.16459153798454257
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.06902011309452065
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.21362126386110467
Processed row 37/10094
ndcg0.01631494205336663
Processed row 38/10094
ndcg0.14554965575329845
Processed row 39/10094
ndcg0.09004110974622696
Processed row 40/10094
ndcg0.2036255047610188
Processed row 41/10094
ndcg0.16047741887355133
Processed row 42/10094
ndcg0.2684217774309127
Processed row 43/10094
ndcg0.12862898507687648
Processed row 44/10094
ndcg0.225209040416297
Processed row 45/10094
ndcg0.11162357774557138
Processed row 46/10094
ndcg0.09046602484955346
Processed row 47/10094
ndcg

ndcg0.04966947480839741
Processed row 209/10094
ndcg0.17909317420164694
Processed row 210/10094
ndcg0.012542316976811518
Processed row 211/10094
ndcg0.187679985808682
Processed row 212/10094
ndcg0.12435567756548703
Processed row 213/10094
ndcg0.08665144280171864
Processed row 214/10094
ndcg0.10049547014642245
Processed row 215/10094
ndcg0.13679591333748894
Processed row 216/10094
ndcg0.08684479364455364
Processed row 217/10094
ndcg0.22823729910815818
Processed row 218/10094
ndcg0.16803756496775035
Processed row 219/10094
ndcg0.022105460852128618
Processed row 220/10094
ndcg0.044080593150064275
Processed row 221/10094
ndcg0.1430128756201286
Processed row 222/10094
ndcg0.2626231896986069
Processed row 223/10094
ndcg0.0866092367139776
Processed row 224/10094
ndcg0.1635424840452836
Processed row 225/10094
ndcg0.1414800358584865
Processed row 226/10094
ndcg0.23306804298053654
Processed row 227/10094
ndcg0.14824942200694177
Processed row 228/10094
ndcg0.03496059011435706
Processed row 229/10

ndcg0.2626231896986069
Processed row 391/10094
ndcg0.06863193501582378
Processed row 392/10094
ndcg0.1200229780858692
Processed row 393/10094
ndcg0.014837476798865245
Processed row 394/10094
ndcg0.033780143618256916
Processed row 395/10094
ndcg0.10013739137758973
Processed row 396/10094
ndcg0.02684088672756094
Processed row 397/10094
ndcg0.0691793084106644
Processed row 398/10094
ndcg0.2543071604599334
Processed row 399/10094
ndcg0.09281326446355109
Processed row 400/10094
ndcg0.30100546170236236
Processed row 401/10094
ndcg0.012542316976811518
Processed row 402/10094
ndcg0.20778527565881522
Processed row 403/10094
ndcg0.13966265197323102
Processed row 404/10094
ndcg0.053291722783785904
Processed row 405/10094
ndcg0.27688521158049423
Processed row 406/10094
ndcg0.17319967180517012
Processed row 407/10094
ndcg0.025354207210232987
Processed row 408/10094
ndcg0.07504199579036192
Processed row 409/10094
ndcg0.11234276719308771
Processed row 410/10094
ndcg0.10051462278072008
Processed row 4

...

ndcg0.20793223207454625
Processed row 9557/10094
ndcg0.2185884040867343
Processed row 9558/10094
ndcg0.12577701864951277
Processed row 9559/10094
ndcg0.11856352904752146
Processed row 9560/10094
ndcg0.2588542762858814
Processed row 9561/10094
ndcg0.15923261417540593
Processed row 9562/10094
ndcg0.2185602074809526
Processed row 9563/10094
ndcg0.1788654762066897
Processed row 9564/10094
ndcg0.15615912800149942
Processed row 9565/10094
ndcg0.0
Processed row 9566/10094
ndcg0.08177712948176916
Processed row 9567/10094
ndcg0.09004110974622696
Processed row 9568/10094
ndcg0.13710626133534728
Processed row 9569/10094
ndcg0.0
Processed row 9570/10094
ndcg0.0
Processed row 9571/10094
ndcg0.09549762833036783
Processed row 9572/10094
ndcg0.12274876052426054
Processed row 9573/10094
ndcg0.022105460852128618
Processed row 9574/10094
ndcg0.08692102540414046
Processed row 9575/10094
ndcg0.02537418620368887
Processed row 9576/10094
ndcg0.17138958003522198
Processed row 9577/10094
ndcg0.0869210254041404

ndcg0.2626231896986069
Processed row 9731/10094
ndcg0.03770999863680709
Processed row 9732/10094
ndcg0.02975313881423611
Processed row 9733/10094
ndcg0.13224495165516986
Processed row 9734/10094
ndcg0.23622697896325123
Processed row 9735/10094
ndcg0.0
Processed row 9736/10094
ndcg0.1412142949261387
Processed row 9737/10094
ndcg0.1904618276997527
Processed row 9738/10094
ndcg0.11428846576954213
Processed row 9739/10094
ndcg0.04253695768177266
Processed row 9740/10094
ndcg0.0
Processed row 9741/10094
ndcg0.03955872398373115
Processed row 9742/10094
ndcg0.20262629561267612
Processed row 9743/10094
ndcg0.0
Processed row 9744/10094
ndcg0.20570636293425068
Processed row 9745/10094
ndcg0.2185884040867343
Processed row 9746/10094
ndcg0.1597782149208785
Processed row 9747/10094
ndcg0.19688333726714896
Processed row 9748/10094
ndcg0.08063839537424852
Processed row 9749/10094
ndcg0.07832661910834837
Processed row 9750/10094
ndcg0.09962261368146662
Processed row 9751/10094
ndcg0.0946279035507496
P

ndcg0.281433073602349
Processed row 9908/10094
ndcg0.3125020083526801
Processed row 9909/10094
ndcg0.1279679621946923
Processed row 9910/10094
ndcg0.0
Processed row 9911/10094
ndcg0.0
Processed row 9912/10094
ndcg0.09335216213713773
Processed row 9913/10094
ndcg0.11681924206761393
Processed row 9914/10094
ndcg0.2969098485624871
Processed row 9915/10094
ndcg0.18956512835777653
Processed row 9916/10094
ndcg0.0
Processed row 9917/10094
ndcg0.15691977513312647
Processed row 9918/10094
ndcg0.03082676044891437
Processed row 9919/10094
ndcg0.3520607323364113
Processed row 9920/10094
ndcg0.32521984560885037
Processed row 9921/10094
ndcg0.1974030132391916
Processed row 9922/10094
ndcg0.12651244599294093
Processed row 9923/10094
ndcg0.1962880099176959
Processed row 9924/10094
ndcg0.08595876911622082
Processed row 9925/10094
ndcg0.07796827715815502
Processed row 9926/10094
ndcg0.3185656819717986
Processed row 9927/10094
ndcg0.12809523781529875
Processed row 9928/10094
ndcg0.19542432548664146
Proc

ndcg0.16172696238207754
Processed row 10085/10094
ndcg0.09166878068101264
Processed row 10086/10094
ndcg0.17319525612972153
Processed row 10087/10094
ndcg0.2129487499566156
Processed row 10088/10094
ndcg0.12266714228191052
Processed row 10089/10094
ndcg0.22547823172871245
Processed row 10090/10094
ndcg0.2588542762858814
Processed row 10091/10094
ndcg0.013438196760869481
Processed row 10092/10094
ndcg0.13003697344252285
Processed row 10093/10094
ndcg0.12161115697371076
Processed row 10094/10094
Average ndcg@10: 0.118366912


0.11836691211629263

In [12]:
calc_ndcg10(info_df, genres, musicnn)

(49, 10094)
ndcg0.17675367210365273
Processed row 1/10094
ndcg0.028317102188593866
Processed row 2/10094
ndcg0.17675367210365273
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.09044120628153834
Processed row 5/10094
ndcg0.2517545506432056
Processed row 6/10094
ndcg0.20526623802871777
Processed row 7/10094
ndcg0.06640050164194333
Processed row 8/10094
ndcg0.05051142906596259
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.20073990205617434
Processed row 11/10094
ndcg0.07498021792817254
Processed row 12/10094
ndcg0.21843593136057138
Processed row 13/10094
ndcg0.19932917462350794
Processed row 14/10094
ndcg0.05605170098294903
Processed row 15/10094
ndcg0.05644042639565183
Processed row 16/10094
ndcg0.16453035488176262
Processed row 17/10094
ndcg0.23352964806329504
Processed row 18/10094
ndcg0.19998331798224175
Processed row 19/10094
ndcg0.0
Processed row 20/10094
ndcg0.054978123398566135
Processed row 21/10094
ndcg0.0
Processed row 22/10094
ndcg0.3023328401476976
Pro

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.2232538353567168
Processed row 26/10094
ndcg0.08662007230724862
Processed row 27/10094
ndcg0.014360346803980361
Processed row 28/10094
ndcg0.37406942521648323
Processed row 29/10094
ndcg0.0
Processed row 30/10094
ndcg0.3720522560064573
Processed row 31/10094
ndcg0.26451691203643424
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.26662732717087895
Processed row 37/10094
ndcg0.08436099996142607
Processed row 38/10094
ndcg0.20168723056238427
Processed row 39/10094
ndcg0.2754474678474013
Processed row 40/10094
ndcg0.1943055357377809
Processed row 41/10094
ndcg0.24090334478777642
Processed row 42/10094
ndcg0.2599731725895505
Processed row 43/10094
ndcg0.15008421809235176
Processed row 44/10094
ndcg0.2729408467147719
Processed row 45/10094
ndcg0.18145816550296476
Processed row 46/10094
ndcg0.12792188990159445
Processed row 47/10094
ndcg0.19350741004162

ndcg0.2874237666348025
Processed row 212/10094
ndcg0.20521146848942937
Processed row 213/10094
ndcg0.0
Processed row 214/10094
ndcg0.2375736499580358
Processed row 215/10094
ndcg0.21249298717603501
Processed row 216/10094
ndcg0.25678171175446096
Processed row 217/10094
ndcg0.31650112683346393
Processed row 218/10094
ndcg0.2710765500398578
Processed row 219/10094
ndcg0.0242718018759376
Processed row 220/10094
ndcg0.016753737937977086
Processed row 221/10094
ndcg0.12379811934834792
Processed row 222/10094
ndcg0.15476566002089595
Processed row 223/10094
ndcg0.11395773674481627
Processed row 224/10094
ndcg0.2611146720650788
Processed row 225/10094
ndcg0.18355122664144458
Processed row 226/10094
ndcg0.16655895328498302
Processed row 227/10094
ndcg0.25357223997590095
Processed row 228/10094
ndcg0.0
Processed row 229/10094
ndcg0.19998331798224175
Processed row 230/10094
ndcg0.29305810766165136
Processed row 231/10094
ndcg0.07735209245478447
Processed row 232/10094
ndcg0.28514276538632916
Proc

ndcg0.0
Processed row 398/10094
ndcg0.20669803846980372
Processed row 399/10094
ndcg0.15190253202417436
Processed row 400/10094
ndcg0.17631357774946124
Processed row 401/10094
ndcg0.05644042639565183
Processed row 402/10094
ndcg0.2335379388507196
Processed row 403/10094
ndcg0.2359320491641322
Processed row 404/10094
ndcg0.09282931996290711
Processed row 405/10094
ndcg0.30945212711998693
Processed row 406/10094
ndcg0.15659541675425645
Processed row 407/10094
ndcg0.06811312350491464
Processed row 408/10094
ndcg0.2796994463765373
Processed row 409/10094
ndcg0.11521950194862124
Processed row 410/10094
ndcg0.21036297874178767
Processed row 411/10094
ndcg0.21974571083809738
Processed row 412/10094
ndcg0.167385697482095
Processed row 413/10094
ndcg0.15782122046442265
Processed row 414/10094
ndcg0.27404293935403956
Processed row 415/10094
ndcg0.18051736026177168
Processed row 416/10094
ndcg0.33667298134934837
Processed row 417/10094
ndcg0.0439210958955116
Processed row 418/10094
ndcg0.29068974

...

ndcg0.24355622092378582
Processed row 9417/10094
ndcg0.16311203548803793
Processed row 9418/10094
ndcg0.2658504431101268
Processed row 9419/10094
ndcg0.35834975608161884
Processed row 9420/10094
ndcg0.3242756275381704
Processed row 9421/10094
ndcg0.08936310768171672
Processed row 9422/10094
ndcg0.061061280018687644
Processed row 9423/10094
ndcg0.2409287652063054
Processed row 9424/10094
ndcg0.0
Processed row 9425/10094
ndcg0.1588195785852091
Processed row 9426/10094
ndcg0.12907330564191236
Processed row 9427/10094
ndcg0.2170764202349565
Processed row 9428/10094
ndcg0.21168900327409973
Processed row 9429/10094
ndcg0.28506691582268484
Processed row 9430/10094
ndcg0.20760932477073987
Processed row 9431/10094
ndcg0.12347863637551228
Processed row 9432/10094
ndcg0.0
Processed row 9433/10094
ndcg0.23637960166864688
Processed row 9434/10094
ndcg0.07498021792817254
Processed row 9435/10094
ndcg0.1340886687260641
Processed row 9436/10094
ndcg0.3292976354740007
Processed row 9437/10094
ndcg0.243

ndcg0.25276058555938435
Processed row 9593/10094
ndcginf
Processed row 9594/10094
ndcg0.05542687577608045
Processed row 9595/10094
ndcg0.13370764776914082
Processed row 9596/10094
ndcg0.0
Processed row 9597/10094
ndcg0.29500935079387863
Processed row 9598/10094
ndcg0.05789979373493211
Processed row 9599/10094
ndcg0.11247127847291037
Processed row 9600/10094
ndcg0.0
Processed row 9601/10094
ndcg0.04873494989028831
Processed row 9602/10094
ndcg0.0
Processed row 9603/10094
ndcg0.03398052262631264
Processed row 9604/10094
ndcg0.0
Processed row 9605/10094
ndcg0.20025257842925473
Processed row 9606/10094
ndcg0.18583430843181228
Processed row 9607/10094
ndcg0.3313021777068291
Processed row 9608/10094
ndcg0.11731902667803232
Processed row 9609/10094
ndcg0.277153130091638
Processed row 9610/10094
ndcg0.1340886687260641
Processed row 9611/10094
ndcg0.3495072373551167
Processed row 9612/10094
ndcg0.34476699773868485
Processed row 9613/10094
ndcg0.0
Processed row 9614/10094
ndcg0.0
Processed row 9

ndcg0.1859143971029669
Processed row 9773/10094
ndcg0.18230842761293284
Processed row 9774/10094
ndcg0.0928841424819625
Processed row 9775/10094
ndcg0.19677699417451078
Processed row 9776/10094
ndcg0.20948263359331176
Processed row 9777/10094
ndcg0.15655722558935978
Processed row 9778/10094
ndcg0.28320332399923576
Processed row 9779/10094
ndcg0.23410055431320206
Processed row 9780/10094
ndcg0.2961186502552112
Processed row 9781/10094
ndcg0.3283167195513694
Processed row 9782/10094
ndcg0.2608878240797371
Processed row 9783/10094
ndcg0.0
Processed row 9784/10094
ndcg0.18686906605814316
Processed row 9785/10094
ndcg0.2556182958890912
Processed row 9786/10094
ndcg0.35417313643068027
Processed row 9787/10094
ndcginf
Processed row 9788/10094
ndcg0.30801270665411123
Processed row 9789/10094
ndcg0.07284406410291873
Processed row 9790/10094
ndcg0.18478758956342978
Processed row 9791/10094
ndcg0.31825543724256095
Processed row 9792/10094
ndcg0.2034280969735022
Processed row 9793/10094
ndcg0.2215

ndcg0.13732452505807208
Processed row 9951/10094
ndcg0.09686355265701264
Processed row 9952/10094
ndcg0.23062233887367514
Processed row 9953/10094
ndcg0.08162276028122983
Processed row 9954/10094
ndcg0.029303693363643725
Processed row 9955/10094
ndcg0.09712137165826824
Processed row 9956/10094
ndcg0.011653530038119019
Processed row 9957/10094
ndcg0.04341571261203987
Processed row 9958/10094
ndcg0.17930585389896114
Processed row 9959/10094
ndcg0.17780019772664343
Processed row 9960/10094
ndcg0.17705869156114418
Processed row 9961/10094
ndcg0.12082915155521676
Processed row 9962/10094
ndcg0.09686355265701264
Processed row 9963/10094
ndcg0.2543256401658902
Processed row 9964/10094
ndcg0.0615736328458691
Processed row 9965/10094
ndcg0.0
Processed row 9966/10094
ndcg0.0
Processed row 9967/10094
ndcg0.07421304616729733
Processed row 9968/10094
ndcg0.15880708630402035
Processed row 9969/10094
ndcg0.13032162247923987
Processed row 9970/10094
ndcg0.0
Processed row 9971/10094
ndcg0.2761903124253

0.1525398502761576

In [13]:
calc_ndcg10(info_df, genres, tfidf)

(999, 10095)
ndcg0.2273507442936581
Processed row 1/10094
ndcg0.0
Processed row 2/10094
ndcg0.13328336696757173
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.06260093684447622
Processed row 5/10094
ndcg0.19215593089762498
Processed row 6/10094
ndcg0.10187662799122997
Processed row 7/10094
ndcg0.044493196474187736
Processed row 8/10094
ndcg0.04352695359527508
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.17212944550220574
Processed row 11/10094
ndcg0.007741292242886216
Processed row 12/10094
ndcg0.15174389489953963
Processed row 13/10094
ndcg0.11523347145665658
Processed row 14/10094
ndcg0.05067591540812202
Processed row 15/10094
ndcg0.009793564558936891
Processed row 16/10094
ndcg0.14342237341910125
Processed row 17/10094
ndcg0.1334159793467815
Processed row 18/10094
ndcg0.22279410222634083
Processed row 19/10094
ndcg0.03823990957302889
Processed row 20/10094
ndcg0.014245184812999115
Processed row 21/10094
ndcg0.042370412336664796
Processed row 22/10094
ndcg0.2

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.12381396621652979
Processed row 26/10094
ndcg0.14355474517801933
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.25770109858064616
Processed row 29/10094
ndcg0.0
Processed row 30/10094
ndcg0.25728717889795677
Processed row 31/10094
ndcg0.18794381747458297
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.17195388885025575
Processed row 37/10094
ndcg0.1207410499907602
Processed row 38/10094
ndcg0.10635601587502302
Processed row 39/10094
ndcg0.25650388333214114
Processed row 40/10094
ndcg0.18164203648499494
Processed row 41/10094
ndcg0.181641245542706
Processed row 42/10094
ndcg0.1925694594244209
Processed row 43/10094
ndcg0.1990638916560653
Processed row 44/10094
ndcg0.20836657423434088
Processed row 45/10094
ndcg0.13231413974211612
Processed row 46/10094
ndcg0.07169543176114068
Processed row 47/10094
ndcg0.13328336696757173
Processed ro

ndcg0.059318892228059646
Processed row 211/10094
ndcg0.21185033062776074
Processed row 212/10094
ndcg0.14371771614482637
Processed row 213/10094
ndcg0.054328930005577376
Processed row 214/10094
ndcg0.3014055842955761
Processed row 215/10094
ndcg0.10898502197035055
Processed row 216/10094
ndcginf
Processed row 217/10094
ndcg0.2102947855208808
Processed row 218/10094
ndcg0.18687093095271098
Processed row 219/10094
ndcg0.0
Processed row 220/10094
ndcg0.0
Processed row 221/10094
ndcg0.07621508631115181
Processed row 222/10094
ndcg0.22261520749794375
Processed row 223/10094
ndcg0.16494362873465054
Processed row 224/10094
ndcg0.25402441695833194
Processed row 225/10094
ndcg0.1631544223103139
Processed row 226/10094
ndcg0.12762412860243766
Processed row 227/10094
ndcg0.1523228425784958
Processed row 228/10094
ndcg0.011366003827372356
Processed row 229/10094
ndcg0.22279410222634083
Processed row 230/10094
ndcg0.19175754723469499
Processed row 231/10094
ndcg0.11361100919330742
Processed row 232

ndcg0.02830230428843225
Processed row 397/10094
ndcg0.030309343539659615
Processed row 398/10094
ndcg0.17290743428945207
Processed row 399/10094
ndcg0.1346646234401166
Processed row 400/10094
ndcg0.1644288761186719
Processed row 401/10094
ndcg0.009793564558936891
Processed row 402/10094
ndcg0.15492377627845577
Processed row 403/10094
ndcg0.16027989965223288
Processed row 404/10094
ndcg0.16679944178132625
Processed row 405/10094
ndcg0.15719675491468715
Processed row 406/10094
ndcg0.09640635817636056
Processed row 407/10094
ndcg0.009217472526058252
Processed row 408/10094
ndcg0.20781406164259789
Processed row 409/10094
ndcg0.09502856177636906
Processed row 410/10094
ndcg0.10135455804865767
Processed row 411/10094
ndcg0.21443783801857155
Processed row 412/10094
ndcg0.11852912606162389
Processed row 413/10094
ndcg0.09380291949730313
Processed row 414/10094
ndcginf
Processed row 415/10094
ndcg0.17697119309548343
Processed row 416/10094
ndcg0.18672728011640735
Processed row 417/10094
ndcg0.0

...

ndcg0.22261520749794375
Processed row 9406/10094
ndcg0.08706019523235731
Processed row 9407/10094
ndcg0.13400200586400374
Processed row 9408/10094
ndcg0.2409710360019434
Processed row 9409/10094
ndcg0.13400200586400374
Processed row 9410/10094
ndcg0.1436172572625088
Processed row 9411/10094
ndcg0.2575845530906395
Processed row 9412/10094
ndcg0.16610207862655565
Processed row 9413/10094
ndcg0.12536943135906822
Processed row 9414/10094
ndcg0.18800095511308004
Processed row 9415/10094
ndcg0.22261520749794375
Processed row 9416/10094
ndcg0.2701502192025614
Processed row 9417/10094
ndcg0.12233708673696728
Processed row 9418/10094
ndcg0.20765494770751444
Processed row 9419/10094
ndcg0.1822845207111849
Processed row 9420/10094
ndcg0.22762413401845313
Processed row 9421/10094
ndcg0.00847855817078014
Processed row 9422/10094
ndcg0.0736659842433415
Processed row 9423/10094
ndcg0.11978629490452442
Processed row 9424/10094
ndcg0.03564692066078405
Processed row 9425/10094
ndcg0.09447468562491028
Pr

ndcg0.018808042516543437
Processed row 9581/10094
ndcg0.15691660294025772
Processed row 9582/10094
ndcg0.25378316004314116
Processed row 9583/10094
ndcg0.10987036964187369
Processed row 9584/10094
ndcg0.1437534828451628
Processed row 9585/10094
ndcg0.0766593900601744
Processed row 9586/10094
ndcg0.02987479279020066
Processed row 9587/10094
ndcg0.0
Processed row 9588/10094
ndcg0.0
Processed row 9589/10094
ndcg0.02530715205307505
Processed row 9590/10094
ndcg0.22256505640479862
Processed row 9591/10094
ndcg0.24545447676137702
Processed row 9592/10094
ndcg0.2241628939750153
Processed row 9593/10094
ndcginf
Processed row 9594/10094
ndcg0.007834851647149513
Processed row 9595/10094
ndcg0.09593358832706746
Processed row 9596/10094
ndcg0.054328930005577376
Processed row 9597/10094
ndcg0.17543645449632403
Processed row 9598/10094
ndcg0.009793564558936891
Processed row 9599/10094
ndcg0.07621508631115181
Processed row 9600/10094
ndcg0.023585253573693538
Processed row 9601/10094
ndcg0.0
Processed

ndcg0.0
Processed row 9761/10094
ndcg0.0
Processed row 9762/10094
ndcg0.0
Processed row 9763/10094
ndcg0.0
Processed row 9764/10094
ndcg0.20280188379664243
Processed row 9765/10094
ndcg0.0
Processed row 9766/10094
ndcg0.0
Processed row 9767/10094
ndcg0.07193346169606893
Processed row 9768/10094
ndcg0.0
Processed row 9769/10094
ndcg0.3014055842955761
Processed row 9770/10094
ndcg0.10860193864800985
Processed row 9771/10094
ndcg0.1644288761186719
Processed row 9772/10094
ndcg0.17623205972094977
Processed row 9773/10094
ndcg0.07738821685443098
Processed row 9774/10094
ndcg0.1416325546821432
Processed row 9775/10094
ndcg0.17192499040193424
Processed row 9776/10094
ndcg0.14007693110820343
Processed row 9777/10094
ndcg0.1044352995089777
Processed row 9778/10094
ndcg0.1615419881157551
Processed row 9779/10094
ndcg0.24148624194435026
Processed row 9780/10094
ndcg0.17236219403056388
Processed row 9781/10094
ndcg0.26845465707695826
Processed row 9782/10094
ndcg0.1575083203889687
Processed row 97

ndcg0.0
Processed row 9937/10094
ndcg0.1369744589585982
Processed row 9938/10094
ndcg0.17578528600466736
Processed row 9939/10094
ndcg0.1447334730899895
Processed row 9940/10094
ndcg0.22585043512442746
Processed row 9941/10094
ndcg0.2498456121995017
Processed row 9942/10094
ndcg0.1658393577230606
Processed row 9943/10094
ndcg0.041986034046734316
Processed row 9944/10094
ndcg0.10066419986684996
Processed row 9945/10094
ndcg0.28317708729771995
Processed row 9946/10094
ndcg0.0
Processed row 9947/10094
ndcg0.10301736982166441
Processed row 9948/10094
ndcg0.17933807794456108
Processed row 9949/10094
ndcg0.2027693953347939
Processed row 9950/10094
ndcg0.10969443728772972
Processed row 9951/10094
ndcg0.03374286940410007
Processed row 9952/10094
ndcg0.23171392474508598
Processed row 9953/10094
ndcg0.03293022071615497
Processed row 9954/10094
ndcg0.09350318824132493
Processed row 9955/10094
ndcg0.09593358832706746
Processed row 9956/10094
ndcg0.12463971070724209
Processed row 9957/10094
ndcg0.0

0.12018254462363298

In [14]:
calc_ndcg10(info_df, genres, bert)

(767, 10095)
ndcg0.2273507442936581
Processed row 1/10094
ndcg0.0
Processed row 2/10094
ndcg0.13328336696757173
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.06260093684447622
Processed row 5/10094
ndcg0.19215593089762498
Processed row 6/10094
ndcg0.10187662799122997
Processed row 7/10094
ndcg0.044493196474187736
Processed row 8/10094
ndcg0.04352695359527508
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.17212944550220574
Processed row 11/10094
ndcg0.007741292242886216
Processed row 12/10094
ndcg0.15174389489953963
Processed row 13/10094
ndcg0.11523347145665658
Processed row 14/10094
ndcg0.05067591540812202
Processed row 15/10094
ndcg0.009793564558936891
Processed row 16/10094
ndcg0.14342237341910125
Processed row 17/10094
ndcg0.1334159793467815
Processed row 18/10094
ndcg0.22279410222634083
Processed row 19/10094
ndcg0.03823990957302889
Processed row 20/10094
ndcg0.014245184812999115
Processed row 21/10094
ndcg0.042370412336664796
Processed row 22/10094
ndcg0.2

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.12381396621652979
Processed row 26/10094
ndcg0.14355474517801933
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.25770109858064616
Processed row 29/10094
ndcg0.0
Processed row 30/10094
ndcg0.25728717889795677
Processed row 31/10094
ndcg0.18794381747458297
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.17195388885025575
Processed row 37/10094
ndcg0.1207410499907602
Processed row 38/10094
ndcg0.10635601587502302
Processed row 39/10094
ndcg0.25650388333214114
Processed row 40/10094
ndcg0.18164203648499494
Processed row 41/10094
ndcg0.181641245542706
Processed row 42/10094
ndcg0.1925694594244209
Processed row 43/10094
ndcg0.1990638916560653
Processed row 44/10094
ndcg0.20836657423434088
Processed row 45/10094
ndcg0.13231413974211612
Processed row 46/10094
ndcg0.07169543176114068
Processed row 47/10094
ndcg0.13328336696757173
Processed ro

ndcg0.059318892228059646
Processed row 211/10094
ndcg0.21185033062776074
Processed row 212/10094
ndcg0.14371771614482637
Processed row 213/10094
ndcg0.054328930005577376
Processed row 214/10094
ndcg0.3014055842955761
Processed row 215/10094
ndcg0.10898502197035055
Processed row 216/10094
ndcginf
Processed row 217/10094
ndcg0.2102947855208808
Processed row 218/10094
ndcg0.18687093095271098
Processed row 219/10094
ndcg0.0
Processed row 220/10094
ndcg0.0
Processed row 221/10094
ndcg0.07621508631115181
Processed row 222/10094
ndcg0.22261520749794375
Processed row 223/10094
ndcg0.16494362873465054
Processed row 224/10094
ndcg0.25402441695833194
Processed row 225/10094
ndcg0.1631544223103139
Processed row 226/10094
ndcg0.12762412860243766
Processed row 227/10094
ndcg0.1523228425784958
Processed row 228/10094
ndcg0.011366003827372356
Processed row 229/10094
ndcg0.22279410222634083
Processed row 230/10094
ndcg0.19175754723469499
Processed row 231/10094
ndcg0.11361100919330742
Processed row 232

ndcg0.02830230428843225
Processed row 397/10094
ndcg0.030309343539659615
Processed row 398/10094
ndcg0.17290743428945207
Processed row 399/10094
ndcg0.1346646234401166
Processed row 400/10094
ndcg0.1644288761186719
Processed row 401/10094
ndcg0.009793564558936891
Processed row 402/10094
ndcg0.15492377627845577
Processed row 403/10094
ndcg0.16027989965223288
Processed row 404/10094
ndcg0.16679944178132625
Processed row 405/10094
ndcg0.15719675491468715
Processed row 406/10094
ndcg0.09640635817636056
Processed row 407/10094
ndcg0.009217472526058252
Processed row 408/10094
ndcg0.20781406164259789
Processed row 409/10094
ndcg0.09502856177636906
Processed row 410/10094
ndcg0.10135455804865767
Processed row 411/10094
ndcg0.21443783801857155
Processed row 412/10094
ndcg0.11852912606162389
Processed row 413/10094
ndcg0.09380291949730313
Processed row 414/10094
ndcginf
Processed row 415/10094
ndcg0.17697119309548343
Processed row 416/10094
ndcg0.18672728011640735
Processed row 417/10094
ndcg0.0

...

ndcg0.13400200586400374
Processed row 9405/10094
ndcg0.22261520749794375
Processed row 9406/10094
ndcg0.08706019523235731
Processed row 9407/10094
ndcg0.13400200586400374
Processed row 9408/10094
ndcg0.2409710360019434
Processed row 9409/10094
ndcg0.13400200586400374
Processed row 9410/10094
ndcg0.1436172572625088
Processed row 9411/10094
ndcg0.2575845530906395
Processed row 9412/10094
ndcg0.16610207862655565
Processed row 9413/10094
ndcg0.12536943135906822
Processed row 9414/10094
ndcg0.18800095511308004
Processed row 9415/10094
ndcg0.22261520749794375
Processed row 9416/10094
ndcg0.2701502192025614
Processed row 9417/10094
ndcg0.12233708673696728
Processed row 9418/10094
ndcg0.20765494770751444
Processed row 9419/10094
ndcg0.1822845207111849
Processed row 9420/10094
ndcg0.22762413401845313
Processed row 9421/10094
ndcg0.00847855817078014
Processed row 9422/10094
ndcg0.0736659842433415
Processed row 9423/10094
ndcg0.11978629490452442
Processed row 9424/10094
ndcg0.03564692066078405
Pr

ndcg0.15960457536186134
Processed row 9579/10094
ndcg0.20618588051952064
Processed row 9580/10094
ndcg0.018808042516543437
Processed row 9581/10094
ndcg0.15691660294025772
Processed row 9582/10094
ndcg0.25378316004314116
Processed row 9583/10094
ndcg0.10987036964187369
Processed row 9584/10094
ndcg0.1437534828451628
Processed row 9585/10094
ndcg0.0766593900601744
Processed row 9586/10094
ndcg0.02987479279020066
Processed row 9587/10094
ndcg0.0
Processed row 9588/10094
ndcg0.0
Processed row 9589/10094
ndcg0.02530715205307505
Processed row 9590/10094
ndcg0.22256505640479862
Processed row 9591/10094
ndcg0.24545447676137702
Processed row 9592/10094
ndcg0.2241628939750153
Processed row 9593/10094
ndcginf
Processed row 9594/10094
ndcg0.007834851647149513
Processed row 9595/10094
ndcg0.09593358832706746
Processed row 9596/10094
ndcg0.054328930005577376
Processed row 9597/10094
ndcg0.17543645449632403
Processed row 9598/10094
ndcg0.009793564558936891
Processed row 9599/10094
ndcg0.076215086311

ndcg0.17828562908452925
Processed row 9759/10094
ndcg0.0
Processed row 9760/10094
ndcg0.0
Processed row 9761/10094
ndcg0.0
Processed row 9762/10094
ndcg0.0
Processed row 9763/10094
ndcg0.0
Processed row 9764/10094
ndcg0.20280188379664243
Processed row 9765/10094
ndcg0.0
Processed row 9766/10094
ndcg0.0
Processed row 9767/10094
ndcg0.07193346169606893
Processed row 9768/10094
ndcg0.0
Processed row 9769/10094
ndcg0.3014055842955761
Processed row 9770/10094
ndcg0.10860193864800985
Processed row 9771/10094
ndcg0.1644288761186719
Processed row 9772/10094
ndcg0.17623205972094977
Processed row 9773/10094
ndcg0.07738821685443098
Processed row 9774/10094
ndcg0.1416325546821432
Processed row 9775/10094
ndcg0.17192499040193424
Processed row 9776/10094
ndcg0.14007693110820343
Processed row 9777/10094
ndcg0.1044352995089777
Processed row 9778/10094
ndcg0.1615419881157551
Processed row 9779/10094
ndcg0.24148624194435026
Processed row 9780/10094
ndcg0.17236219403056388
Processed row 9781/10094
ndcg0.

ndcg0.0
Processed row 9935/10094
ndcg0.12817892478474868
Processed row 9936/10094
ndcg0.0
Processed row 9937/10094
ndcg0.1369744589585982
Processed row 9938/10094
ndcg0.17578528600466736
Processed row 9939/10094
ndcg0.1447334730899895
Processed row 9940/10094
ndcg0.22585043512442746
Processed row 9941/10094
ndcg0.2498456121995017
Processed row 9942/10094
ndcg0.1658393577230606
Processed row 9943/10094
ndcg0.041986034046734316
Processed row 9944/10094
ndcg0.10066419986684996
Processed row 9945/10094
ndcg0.28317708729771995
Processed row 9946/10094
ndcg0.0
Processed row 9947/10094
ndcg0.10301736982166441
Processed row 9948/10094
ndcg0.17933807794456108
Processed row 9949/10094
ndcg0.2027693953347939
Processed row 9950/10094
ndcg0.10969443728772972
Processed row 9951/10094
ndcg0.03374286940410007
Processed row 9952/10094
ndcg0.23171392474508598
Processed row 9953/10094
ndcg0.03293022071615497
Processed row 9954/10094
ndcg0.09350318824132493
Processed row 9955/10094
ndcg0.09593358832706746

0.12018254462363298

In [15]:
calc_ndcg10(info_df, genres, word2vec)

(299, 10095)
ndcg0.051032634619024936
Processed row 1/10094
ndcg0.15903332297611722
Processed row 2/10094
ndcg0.051032634619024936
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.13785630894803436
Processed row 5/10094
ndcg0.0957998739015808
Processed row 6/10094
ndcg0.21009410605473475
Processed row 7/10094
ndcg0.0
Processed row 8/10094
ndcg0.0
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.019783302398486996
Processed row 11/10094
ndcg0.069789572990852
Processed row 12/10094
ndcg0.0701996508585633
Processed row 13/10094
ndcg0.11705944127406577
Processed row 14/10094
ndcg0.03583288279456539
Processed row 15/10094
ndcg0.0
Processed row 16/10094
ndcg0.04277525622661297
Processed row 17/10094
ndcg0.18950464616663537
Processed row 18/10094
ndcg0.0707765205153477
Processed row 19/10094
ndcg0.037626950930434555
Processed row 20/10094
ndcg0.010451930814009597
Processed row 21/10094
ndcg0.04031459028260845
Processed row 22/10094
ndcg0.14131837033343228
Processed row 23/1

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.1296143231844135
Processed row 26/10094
ndcg0.0919275103245854
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.14672392051266608
Processed row 29/10094
ndcg0.01710315951383389
Processed row 30/10094
ndcg0.15362108885337614
Processed row 31/10094
ndcg0.10647990823844683
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.10851448749231618
Processed row 37/10094
ndcg0.023739962878184393
Processed row 38/10094
ndcg0.0759194587012651
Processed row 39/10094
ndcg0.05567926640681642
Processed row 40/10094
ndcg0.1184115228295919
Processed row 41/10094
ndcg0.0769008285771653
Processed row 42/10094
ndcg0.18966340444574428
Processed row 43/10094
ndcg0.07221245694763745
Processed row 44/10094
ndcg0.17839987048417927
Processed row 45/10094
ndcg0.059481734021527774
Processed row 46/10094
ndcg0.08113276967994416
Processed row 47/10094
ndcg0.051032634619

ndcg0.11882195030663542
Processed row 209/10094
ndcg0.1376719363413635
Processed row 210/10094
ndcg0.0
Processed row 211/10094
ndcg0.10999084931151448
Processed row 212/10094
ndcg0.0639400867862814
Processed row 213/10094
ndcg0.09406737732608637
Processed row 214/10094
ndcg0.059415820608494374
Processed row 215/10094
ndcg0.125925131357126
Processed row 216/10094
ndcginf
Processed row 217/10094
ndcg0.15735072331752029
Processed row 218/10094
ndcg0.1262842183084193
Processed row 219/10094
ndcg0.09392666615857241
Processed row 220/10094
ndcg0.0
Processed row 221/10094
ndcg0.20215455992820486
Processed row 222/10094
ndcg0.11595338911802264
Processed row 223/10094
ndcg0.03529400781443094
Processed row 224/10094
ndcg0.07477259749720933
Processed row 225/10094
ndcg0.04278116346165866
Processed row 226/10094
ndcg0.16562593890970628
Processed row 227/10094
ndcg0.10897256343548034
Processed row 228/10094
ndcg0.0
Processed row 229/10094
ndcg0.0707765205153477
Processed row 230/10094
ndcg0.1272565

ndcg0.07586822283862453
Processed row 395/10094
ndcg0.05896522970839802
Processed row 396/10094
ndcg0.04606235694135691
Processed row 397/10094
ndcg0.0
Processed row 398/10094
ndcg0.18861862468409524
Processed row 399/10094
ndcg0.06725096274623824
Processed row 400/10094
ndcg0.13758599006507027
Processed row 401/10094
ndcg0.0
Processed row 402/10094
ndcg0.17960603523220942
Processed row 403/10094
ndcg0.04278116346165866
Processed row 404/10094
ndcg0.07192301088142426
Processed row 405/10094
ndcg0.19427053710469946
Processed row 406/10094
ndcg0.1075514891301693
Processed row 407/10094
ndcg0.1983823054632852
Processed row 408/10094
ndcg0.0664671614480183
Processed row 409/10094
ndcg0.06661519177334982
Processed row 410/10094
ndcg0.08641669787752163
Processed row 411/10094
ndcg0.0637281895306449
Processed row 412/10094
ndcg0.1540510501857173
Processed row 413/10094
ndcg0.14339927012437667
Processed row 414/10094
ndcginf
Processed row 415/10094
ndcg0.10286089209896455
Processed row 416/100

...

ndcg0.0
Processed row 9391/10094
ndcg0.03541893027299952
Processed row 9392/10094
ndcg0.17234104545941223
Processed row 9393/10094
ndcg0.16271701817659193
Processed row 9394/10094
ndcg0.09904833881850177
Processed row 9395/10094
ndcg0.07702911442721118
Processed row 9396/10094
ndcg0.09713991365280535
Processed row 9397/10094
ndcg0.01819511449389369
Processed row 9398/10094
ndcg0.0
Processed row 9399/10094
ndcg0.1443807825839676
Processed row 9400/10094
ndcg0.11701080175715825
Processed row 9401/10094
ndcg0.1234171964339881
Processed row 9402/10094
ndcg0.04703368866304319
Processed row 9403/10094
ndcg0.023739962878184393
Processed row 9404/10094
ndcg0.039632518210007385
Processed row 9405/10094
ndcg0.11595338911802264
Processed row 9406/10094
ndcg0.22650484938838192
Processed row 9407/10094
ndcg0.039632518210007385
Processed row 9408/10094
ndcg0.12463187682826067
Processed row 9409/10094
ndcg0.039632518210007385
Processed row 9410/10094
ndcg0.0925787247981797
Processed row 9411/10094
nd

ndcg0.13933360949237544
Processed row 9565/10094
ndcg0.02094702606898623
Processed row 9566/10094
ndcg0.0819688289437314
Processed row 9567/10094
ndcg0.05567926640681642
Processed row 9568/10094
ndcg0.15690941238058742
Processed row 9569/10094
ndcg0.04341571261203987
Processed row 9570/10094
ndcg0.035275266497282395
Processed row 9571/10094
ndcg0.06820817478051495
Processed row 9572/10094
ndcg0.07599572782953248
Processed row 9573/10094
ndcg0.09392666615857241
Processed row 9574/10094
ndcg0.08143387407332696
Processed row 9575/10094
ndcg0.057992055786324354
Processed row 9576/10094
ndcg0.16940916652990218
Processed row 9577/10094
ndcg0.10831026759506594
Processed row 9578/10094
ndcg0.08051908416940297
Processed row 9579/10094
ndcg0.09040757144153115
Processed row 9580/10094
ndcg0.014471904204013291
Processed row 9581/10094
ndcg0.09077744894158664
Processed row 9582/10094
ndcg0.15544753285762486
Processed row 9583/10094
ndcg0.04676248133742564
Processed row 9584/10094
ndcg0.039632518210

ndcg0.14370155554648995
Processed row 9743/10094
ndcg0.0
Processed row 9744/10094
ndcg0.12296318551852221
Processed row 9745/10094
ndcg0.05662729935901532
Processed row 9746/10094
ndcg0.07600547570367527
Processed row 9747/10094
ndcg0.1443807825839676
Processed row 9748/10094
ndcg0.03729480522765221
Processed row 9749/10094
ndcg0.06148485984229954
Processed row 9750/10094
ndcg0.09282059414987824
Processed row 9751/10094
ndcg0.0533683074918166
Processed row 9752/10094
ndcg0.12692732781430716
Processed row 9753/10094
ndcg0.03135579244202879
Processed row 9754/10094
ndcg0.0
Processed row 9755/10094
ndcg0.09514068515253296
Processed row 9756/10094
ndcg0.12131461541761689
Processed row 9757/10094
ndcg0.051032634619024936
Processed row 9758/10094
ndcg0.1773134207631392
Processed row 9759/10094
ndcg0.0
Processed row 9760/10094
ndcg0.0
Processed row 9761/10094
ndcg0.0
Processed row 9762/10094
ndcg0.0
Processed row 9763/10094
ndcg0.0
Processed row 9764/10094
ndcg0.09424408230838892
Processed ro

ndcg0.1856114605118253
Processed row 9921/10094
ndcg0.1376719363413635
Processed row 9922/10094
ndcg0.17242367863420174
Processed row 9923/10094
ndcg0.1702727369491191
Processed row 9924/10094
ndcg0.075286160918253
Processed row 9925/10094
ndcg0.03709019995405401
Processed row 9926/10094
ndcg0.2396133771090346
Processed row 9927/10094
ndcg0.11614562758119182
Processed row 9928/10094
ndcg0.14200977314749635
Processed row 9929/10094
ndcg0.09073659905983825
Processed row 9930/10094
ndcg0.0
Processed row 9931/10094
ndcg0.20523694841876838
Processed row 9932/10094
ndcg0.10357098956990188
Processed row 9933/10094
ndcg0.01710315951383389
Processed row 9934/10094
ndcg0.11871873269350876
Processed row 9935/10094
ndcg0.13750179656684008
Processed row 9936/10094
ndcg0.0
Processed row 9937/10094
ndcg0.16677782673918973
Processed row 9938/10094
ndcg0.11478608032999162
Processed row 9939/10094
ndcg0.09728715264577009
Processed row 9940/10094
ndcg0.0637281895306449
Processed row 9941/10094
ndcg0.0637

0.08918110725065266

In [16]:
calc_ndcg10(info_df, genres, vgg19)

(8191, 10094)
ndcg0.16420371667798608
Processed row 1/10094
ndcg0.028317102188593866
Processed row 2/10094
ndcg0.16420371667798608
Processed row 3/10094
ndcg0.0
Processed row 4/10094
ndcg0.08648606881405552
Processed row 5/10094
ndcg0.24787004063049928
Processed row 6/10094
ndcg0.19290643344283395
Processed row 7/10094
ndcg0.06640050164194333
Processed row 8/10094
ndcg0.04031459028260845
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.20073990205617434
Processed row 11/10094
ndcg0.06410358989259479
Processed row 12/10094
ndcg0.20360416585751082
Processed row 13/10094
ndcg0.19544466461080162
Processed row 14/10094
ndcg0.05605170098294903
Processed row 15/10094
ndcg0.05644042639565183
Processed row 16/10094
ndcg0.1334542747801119
Processed row 17/10094
ndcg0.2341571458345784
Processed row 18/10094
ndcg0.16502272786788466
Processed row 19/10094
ndcg0.0
Processed row 20/10094
ndcg0.054978123398566135
Processed row 21/10094
ndcg0.0
Processed row 22/10094
ndcg0.3000668759736189
Pr

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.2028601577900085
Processed row 26/10094
ndcg0.07243316617388634
Processed row 27/10094
ndcg0.014360346803980361
Processed row 28/10094
ndcg0.35528252224593987
Processed row 29/10094
ndcg0.02719157008894438
Processed row 30/10094
ndcg0.3596924514205735
Processed row 31/10094
ndcg0.2540028382687091
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.0
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.26374821974969664
Processed row 37/10094
ndcg0.08436099996142607
Processed row 38/10094
ndcg0.19792224393468427
Processed row 39/10094
ndcg0.2562534183728523
Processed row 40/10094
ndcg0.17422560705671428
Processed row 41/10094
ndcg0.22924981474965742
Processed row 42/10094
ndcg0.2385495113073519
Processed row 43/10094
ndcg0.13089016861780278
Processed row 44/10094
ndcg0.2528609180337053
Processed row 45/10094
ndcg0.15086764915290232
Processed row 46/10094
ndcg0.11832486516431996
Processed row 47/10094
ndcg

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: invalid value encountered in double_scalars
  ndcg = dcg / idcg


ndcg0.1775753397098597
Processed row 153/10094
ndcg0.2934782293139386
Processed row 154/10094
ndcg0.2672668337740839
Processed row 155/10094
ndcg0.23771134843826072
Processed row 156/10094
ndcg0.3984477009075426
Processed row 157/10094
ndcg0.18095745461596316
Processed row 158/10094
ndcg0.12811288886845235
Processed row 159/10094
ndcg0.3556986438215681
Processed row 160/10094
ndcg0.12407000542248023
Processed row 161/10094
ndcg0.26894469550396577
Processed row 162/10094
ndcg0.3132146152013158
Processed row 163/10094
ndcg0.13038691517479287
Processed row 164/10094
ndcg0.23532405443969598
Processed row 165/10094
ndcg0.19963410858102046
Processed row 166/10094
ndcg0.0
Processed row 167/10094
ndcg0.21263796506536287
Processed row 168/10094
ndcg0.13153741333550015
Processed row 169/10094
ndcg0.18315075503934916
Processed row 170/10094
ndcg0.05797169262128114
Processed row 171/10094
ndcg0.2555389039200073
Processed row 172/10094
ndcg0.20538745783768922
Processed row 173/10094
ndcg0.171751564

...

ndcg0.2112796908173136
Processed row 9434/10094
ndcg0.06410358989259479
Processed row 9435/10094
ndcg0.17592185347828623
Processed row 9436/10094
ndcg0.3129826934206341
Processed row 9437/10094
ndcg0.24434270361517518
Processed row 9438/10094
ndcg0.26084462012481197
Processed row 9439/10094
ndcg0.1872064145114208
Processed row 9440/10094
ndcg0.20471485757865848
Processed row 9441/10094
ndcg0.0
Processed row 9442/10094
ndcg0.11628287588903338
Processed row 9443/10094
ndcg0.1311477141467366
Processed row 9444/10094
ndcg0.21028698298773776
Processed row 9445/10094
ndcg0.19696019155432082
Processed row 9446/10094
ndcg0.13477792238773925
Processed row 9447/10094
ndcg0.27903479702141565
Processed row 9448/10094
ndcg0.2041286305537255
Processed row 9449/10094
ndcg0.19708389179064204
Processed row 9450/10094
ndcg0.2321799325422616
Processed row 9451/10094
ndcg0.1547367804894055
Processed row 9452/10094
ndcg0.19228124382335887
Processed row 9453/10094
ndcg0.2785096335711502
Processed row 9454/1

ndcg0.2590254166990084
Processed row 9610/10094
ndcg0.14873028338934186
Processed row 9611/10094
ndcg0.31901971937660334
Processed row 9612/10094
ndcg0.3331134677005659
Processed row 9613/10094
ndcg0.0
Processed row 9614/10094
ndcg0.0
Processed row 9615/10094
ndcg0.05572538027979988
Processed row 9616/10094
ndcg0.1762365268845578
Processed row 9617/10094
ndcg0.18757033000643392
Processed row 9618/10094
ndcg0.3402077809215057
Processed row 9619/10094
ndcg0.16502272786788466
Processed row 9620/10094
ndcg0.14873028338934186
Processed row 9621/10094
ndcg0.11832486516431996
Processed row 9622/10094
ndcg0.13038691517479287
Processed row 9623/10094
ndcg0.26897495627400736
Processed row 9624/10094
ndcg0.15027376594435687
Processed row 9625/10094
ndcg0.0
Processed row 9626/10094
ndcg0.0
Processed row 9627/10094
ndcg0.1517596789125648
Processed row 9628/10094
ndcg0.0
Processed row 9629/10094
ndcg0.2496242204576559
Processed row 9630/10094
ndcg0.1885684042449365
Processed row 9631/10094
ndcg0.149

ndcg0.07956198141901089
Processed row 9790/10094
ndcg0.18478758956342978
Processed row 9791/10094
ndcg0.3066019072044419
Processed row 9792/10094
ndcg0.1762365268845578
Processed row 9793/10094
ndcg0.21069507432457404
Processed row 9794/10094
ndcg0.15911948701509848
Processed row 9795/10094
ndcg0.2885178869602781
Processed row 9796/10094
ndcg0.0
Processed row 9797/10094
ndcg0.31264495121981667
Processed row 9798/10094
ndcg0.018878068125729244
Processed row 9799/10094
ndcg0.0
Processed row 9800/10094
ndcg0.27132270533255726
Processed row 9801/10094
ndcg0.0
Processed row 9802/10094
ndcg0.24505178792225954
Processed row 9803/10094
ndcg0.23626106378348685
Processed row 9804/10094
ndcg0.14873028338934186
Processed row 9805/10094
ndcg0.08092979928181797
Processed row 9806/10094
ndcg0.09686355265701264
Processed row 9807/10094
ndcg0.0
Processed row 9808/10094
ndcg0.2917026837163251
Processed row 9809/10094
ndcg0.0
Processed row 9810/10094
ndcg0.22641291110278805
Processed row 9811/10094
ndcg0

ndcg0.07421304616729733
Processed row 9968/10094
ndcg0.15064961527733703
Processed row 9969/10094
ndcg0.1745079238737745
Processed row 9970/10094
ndcg0.0
Processed row 9971/10094
ndcg0.26453678238727873
Processed row 9972/10094
ndcg0.13329271341679058
Processed row 9973/10094
ndcg0.021707856306019936
Processed row 9974/10094
ndcg0.0
Processed row 9975/10094
ndcg0.0
Processed row 9976/10094
ndcg0.0
Processed row 9977/10094
ndcg0.28520704956713333
Processed row 9978/10094
ndcg0.09368941978269793
Processed row 9979/10094
ndcg0.0
Processed row 9980/10094
ndcg0.17379975908315703
Processed row 9981/10094
ndcg0.1981418257139889
Processed row 9982/10094
ndcg0.27261814657154226
Processed row 9983/10094
ndcg0.0
Processed row 9984/10094
ndcg0.3113067949191639
Processed row 9985/10094
ndcg0.1517596789125648
Processed row 9986/10094
ndcg0.3188899011397507
Processed row 9987/10094
ndcg0.18959572916211614
Processed row 9988/10094
ndcg0.17379975908315703
Processed row 9989/10094
ndcg0.3593655842131027

0.14624399362004856

## Random Baseline

In [62]:
import random
def calc_ndcg10_random(df, all_genres):

    # Define the value of k
    k = 10
    
    all_track_ids = info_df.id.unique()

    # Define an empty list to store the ndcg scores
    ndcg_scores = []

    # Loop over each query track
    for idx, query_id in enumerate(df.id):
        # Randomly select k tracks (excluding the query track itself)
        similar_tracks_indices = random.sample(list(all_track_ids), k)
        
        # Ensure that query_id is not in similar_tracks_indices
        if query_id in similar_tracks_indices:
            similar_tracks_indices.remove(query_id)
        
        # Calculate ndcg score 
        ndcg = ndcg_score(query_id, similar_tracks_indices, genres)
    
        # Append the ndcg score to the list
        ndcg_scores.append(ndcg)

        # Print progress
        print(f'Processed row {idx+1}/{len(df)}')

    # Calculate the ndcg over all query tracks
    ndcg_scores = [0 if np.isnan(x) or np.isinf(x) else x for x in ndcg_scores]
    avg_ndcg = np.mean(ndcg_scores)

    # Print the result
    print(f'Average ndcg@{k}: {avg_ndcg:.9f}')

    return avg_ndcg

In [63]:
calc_ndcg10_random(info_df, genres)

ndcg0.11699115252571768
Processed row 1/10094
ndcg0.14009375057929074
Processed row 2/10094
ndcg0.16866336636378904
Processed row 3/10094
ndcg0.05644042639565183
Processed row 4/10094
ndcg0.15214247855192076
Processed row 5/10094
ndcg0.21311233998568377
Processed row 6/10094
ndcg0.24811138187260479
Processed row 7/10094
ndcg0.09053100975743651
Processed row 8/10094
ndcg0.049888154818595355
Processed row 9/10094
ndcg0.0
Processed row 10/10094
ndcg0.11909077480921391
Processed row 11/10094
ndcg0.05321316928378708
Processed row 12/10094
ndcg0.22563686194986957
Processed row 13/10094
ndcg0.1200639357500872
Processed row 14/10094
ndcg0.10375730482280032
Processed row 15/10094
ndcg0.016600125410485833
Processed row 16/10094
ndcg0.07490945498014498
Processed row 17/10094
ndcg0.1419229371861223
Processed row 18/10094
ndcg0.2029718777281118
Processed row 19/10094
ndcg0.08461829868373175
Processed row 20/10094
ndcg0.048208635924849474
Processed row 21/10094
ndcg0.0
Processed row 22/10094
ndcg0.3

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: divide by zero encountered in double_scalars
  ndcg = dcg / idcg


ndcginf
Processed row 25/10094
ndcg0.19358848700248188
Processed row 26/10094
ndcg0.1311833643305745
Processed row 27/10094
ndcg0.0
Processed row 28/10094
ndcg0.23851806299898365
Processed row 29/10094
ndcg0.10934163658384542
Processed row 30/10094
ndcg0.3323313245878811
Processed row 31/10094
ndcg0.33829553513575716
Processed row 32/10094
ndcg0.0
Processed row 33/10094
ndcg0.0
Processed row 34/10094
ndcg0.02565473927075083
Processed row 35/10094
ndcg0.0
Processed row 36/10094
ndcg0.18146837136459065
Processed row 37/10094
ndcg0.03028532876595179
Processed row 38/10094
ndcg0.11423009305509238
Processed row 39/10094
ndcg0.18406063110059429
Processed row 40/10094
ndcg0.14833703871773757
Processed row 41/10094
ndcg0.24399325225794632
Processed row 42/10094
ndcg0.16572920882204573
Processed row 43/10094
ndcg0.1593871078713138
Processed row 44/10094
ndcg0.19366055788643036
Processed row 45/10094
ndcg0.1534802278386091
Processed row 46/10094
ndcg0.1177103729775814
Processed row 47/10094
ndcg

ndcg0.1225748681352878
Processed row 208/10094
ndcg0.038248183855497
Processed row 209/10094
ndcg0.25353822668678416
Processed row 210/10094
ndcg0.0
Processed row 211/10094
ndcg0.23723997146120365
Processed row 212/10094
ndcg0.19614320750803274
Processed row 213/10094
ndcg0.00999427136068019
Processed row 214/10094
ndcg0.31707500699840824
Processed row 215/10094
ndcg0.1309101353372467
Processed row 216/10094
ndcginf
Processed row 217/10094
ndcg0.2117091352394501
Processed row 218/10094
ndcg0.24337002283968875
Processed row 219/10094
ndcg0.013696132429721767
Processed row 220/10094
ndcg0.01812771339262959
Processed row 221/10094
ndcg0.1038572088584318
Processed row 222/10094
ndcg0.27191189373556895
Processed row 223/10094
ndcg0.07873573961738911
Processed row 224/10094
ndcg0.1572050591367307
Processed row 225/10094
ndcg0.266919647161363
Processed row 226/10094
ndcg0.051720737049435445
Processed row 227/10094
ndcg0.2211341892550371
Processed row 228/10094
ndcg0.009597024737274487
Process

/var/folders/tg/y46vr_z93zbfsfkdwgw1xff40000gp/T/ipykernel_94753/2613456094.py:31: RuntimeWarning: invalid value encountered in double_scalars
  ndcg = dcg / idcg


...

ndcg0.028220213197825916
Processed row 9542/10094
ndcg0.1534414808528181
Processed row 9543/10094
ndcg0.04256012342255108
Processed row 9544/10094
ndcg0.19158487738109206
Processed row 9545/10094
ndcg0.08787269737014237
Processed row 9546/10094
ndcg0.2780717849245189
Processed row 9547/10094
ndcg0.1417542079219578
Processed row 9548/10094
ndcg0.20978195818909623
Processed row 9549/10094
ndcg0.32258005860587474
Processed row 9550/10094
ndcg0.014158551094296933
Processed row 9551/10094
ndcg0.14548838903392353
Processed row 9552/10094
ndcg0.018698129674056936
Processed row 9553/10094
ndcg0.17679405440627122
Processed row 9554/10094
ndcg0.0
Processed row 9555/10094
ndcg0.3295693472561112
Processed row 9556/10094
ndcg0.3031080834319513
Processed row 9557/10094
ndcg0.13650478654956025
Processed row 9558/10094
ndcg0.1508007355504187
Processed row 9559/10094
ndcg0.09960608404529445
Processed row 9560/10094
ndcg0.22996251600189468
Processed row 9561/10094
ndcg0.2568669785110963
Processed row 95

ndcg0.09303914967987613
Processed row 9715/10094
ndcg0.1326807852837769
Processed row 9716/10094
ndcg0.06661920758044204
Processed row 9717/10094
ndcg0.2101274926467957
Processed row 9718/10094
ndcg0.21454608776903045
Processed row 9719/10094
ndcginf
Processed row 9720/10094
ndcg0.2756326256939788
Processed row 9721/10094
ndcg0.0
Processed row 9722/10094
ndcg0.10252373276542502
Processed row 9723/10094
ndcg0.13653170657134278
Processed row 9724/10094
ndcg0.12740767704556133
Processed row 9725/10094
ndcg0.170082802035296
Processed row 9726/10094
ndcg0.1292144679725095
Processed row 9727/10094
ndcg0.03796793430565936
Processed row 9728/10094
ndcg0.0
Processed row 9729/10094
ndcg0.052458716433495124
Processed row 9730/10094
ndcg0.06642472641235769
Processed row 9731/10094
ndcg0.0
Processed row 9732/10094
ndcg0.0
Processed row 9733/10094
ndcg0.23850622751183534
Processed row 9734/10094
ndcg0.1321039422677771
Processed row 9735/10094
ndcg0.0
Processed row 9736/10094
ndcg0.08459708270290235


ndcg0.24082960410210044
Processed row 9892/10094
ndcg0.07345022974553157
Processed row 9893/10094
ndcg0.22564572819904377
Processed row 9894/10094
ndcg0.05903232459293636
Processed row 9895/10094
ndcg0.13127955065999122
Processed row 9896/10094
ndcg0.054541326233529475
Processed row 9897/10094
ndcg0.09602575840551543
Processed row 9898/10094
ndcg0.12416477583731736
Processed row 9899/10094
ndcg0.0
Processed row 9900/10094
ndcg0.09139276932944675
Processed row 9901/10094
ndcg0.22201460578557372
Processed row 9902/10094
ndcg0.04703368866304319
Processed row 9903/10094
ndcg0.10467859610565068
Processed row 9904/10094
ndcg0.13342409545708112
Processed row 9905/10094
ndcg0.14813378590031276
Processed row 9906/10094
ndcginf
Processed row 9907/10094
ndcg0.19826628320048303
Processed row 9908/10094
ndcg0.32873261019520594
Processed row 9909/10094
ndcg0.19263178280617382
Processed row 9910/10094
ndcg0.0489942805382056
Processed row 9911/10094
ndcg0.08516852907469441
Processed row 9912/10094
ndc

ndcg0.035275266497282395
Processed row 10066/10094
ndcg0.0999171837211826
Processed row 10067/10094
ndcg0.05866023163137422
Processed row 10068/10094
ndcg0.0
Processed row 10069/10094
ndcg0.05644042639565183
Processed row 10070/10094
ndcg0.05097690880625859
Processed row 10071/10094
ndcg0.11890611894539113
Processed row 10072/10094
ndcg0.12324582898129015
Processed row 10073/10094
ndcg0.031816451775598054
Processed row 10074/10094
ndcg0.0
Processed row 10075/10094
ndcg0.16072061475045865
Processed row 10076/10094
ndcg0.165420752300329
Processed row 10077/10094
ndcg0.0
Processed row 10078/10094
ndcg0.02713432919059125
Processed row 10079/10094
ndcg0.058505751584210106
Processed row 10080/10094
ndcg0.0
Processed row 10081/10094
ndcg0.045861291923765306
Processed row 10082/10094
ndcg0.2976560062071993
Processed row 10083/10094
ndcg0.16266318297048943
Processed row 10084/10094
ndcg0.19717834673180584
Processed row 10085/10094
ndcg0.29411241965888685
Processed row 10086/10094
ndcg0.17232948

0.12053257303802335

# Early Fusion 

In [46]:
import umap.umap_ as umap
reducer = umap.UMAP()

In [47]:
def make2embeddings1(embedding1, embedding2):
    embedding_array = data_fusion(embedding1.head(10094),embedding2 )
    #Apply UMAP
    # Convert to NumPy array
    embedding_array = np.asarray(embedding_array)
    umap_model = umap.UMAP(n_neighbors=4, min_dist=0.8, n_components=100)  # Adjust parameters as needed
    print("Starting UMAP")
    embedding_umap = umap_model.fit_transform(embedding_array)
    print("Stopping UMAP")
    # Convert the UMAP result to a matrix
    embedding_matrix = np.matrix(embedding_umap)
    return embedding_matrix, embedding_matrix.transpose()

In [48]:
def generate_cos_sim_matrix2(embedding1, embedding2):
    print(embedding1.shape)
    print(embedding2.shape)
    #embedding1.drop(7298, axis=0, inplace=True)
    #embedding2.drop(7298, axis=0, inplace=True)
    embedding_matrix,embedding_transpose = make2embeddings1(embedding1, embedding2)
    #embedding_matrix,embedding_transpose = convert2matrix(embedding)


    # Überprüfen Sie die Form der transponierten Matrizen
    print(embedding_matrix.shape) # (1328, 10093)
    #print(len(blf_correlation), len(blf_correlation_transpose_zip[0])) # (1328, 10093)
    # Berechnen Sie die Kosinusähnlichkeitsmatrix
    cos_sim_matrix = np.triu(embedding_matrix.dot(embedding_transpose) / (np.linalg.norm(embedding_matrix, axis=1) * np.linalg.norm(embedding_matrix, axis=1)[:, None]))
    # Fill the lower triangular part with the same values as the upper triangular part
    cos_sim_matrix = cos_sim_matrix + cos_sim_matrix.T - np.diag(cos_sim_matrix.diagonal())

    # Create a dataframe from the numpy matrix
    df = pd.DataFrame(cos_sim_matrix)

    # Assign the ids to the index and columns
    df.index = embedding1.iloc[:, 0]
    #df.index = df.index.str.strip('(),')
    df.columns = embedding1.iloc[:, 0]
    #df.columns = df.columns.str.strip('(),')

    return df

In [49]:
def data_fusion(embedding1, embedding2):
    matrix1, matrix1b = convert2matrix(embedding1)
    matrix2, matrix2b = convert2matrix(embedding2)

    # Ensure the matrices have the same number of rows
    if matrix1.shape[0] != matrix2.shape[0]:
        raise ValueError("Matrices must have the same number of rows for concatenation.")

    # Horizontally stack the matrices
    fused_matrix = np.hstack((matrix1, matrix2))

    return fused_matrix

In [50]:
def convert2matrix(embedding):
    embedding = embedding.sort_values(by='id')
    # Konvertieren Sie den DataFrame in ein NumPy-ndarray
    embedding_array = embedding.iloc[:, 2:].to_numpy()
    # Konvertieren Sie das NumPy-ndarray in eine NumPy-Matrix
    # initialize the LDA model with the desired parameters
    #lda = LatentDirichletAllocation(n_components=50, max_iter=5, learning_method='online', learning_offset=50., random_state=0)

    '''# Apply UMAP
    umap_model = umap.UMAP(n_neighbors=10, min_dist=0.2, n_components=50)  # Adjust parameters as needed
    print("Starting UMAP")
    embedding_umap = umap_model.fit_transform(embedding_array)
    print("Stopping UMAP")'''
    
    # Convert the UMAP result to a matrix
    embedding_matrix = np.matrix(embedding_array)
    
    # Transponieren Sie die Matrix mit der transpose() Methode
    #embedding_transpose = embedding_matrix.transpose()
    #embedding_mm_fused = data_fusion(tfidf[:10094], musicnn)
    # Transponieren Sie die Matrix mit der transpose() Methode
    embedding_transpose = embedding_matrix.transpose()
    return embedding_matrix,embedding_transpose

In [57]:
#preprocess dataset
bert = bert[bert['id'] != '03Oc9WeMEmyLLQbj']

In [68]:
genres = genres[genres['id'] != '03Oc9WeMEmyLLQbj']

In [58]:
fusion_bert_musicnn = generate_cos_sim_matrix2(bert,musicnn)

(10094, 769)
(10094, 51)
Starting UMAP
Stopping UMAP
(10094, 100)


In [59]:
def calc_ndcg_at_10_fusion(df, all_genres, embedding):
    # Define the value of k
    k = 10

    # Define an empty list to store the ndcg scores
    ndcg_scores = []
    
    cos_sim_matrix = embedding

    # Loop over each query track
    for idx, query_id in enumerate(df.id):

        # Get the top-k most similar tracks using the cosine similarity matrix
        similar_tracks_indices = random_baseline(query_id, info, 10)
        
        # Calculate ndcg score 
        ndcg = ndcg_score(query_id, similar_tracks_indices, genres)
    
        # Append the ndcg score to the list
        ndcg_scores.append(ndcg)

        # Print progress
        print(f'Processed row {idx+1}/{len(df)}')

    # Calculate the ndcg over all query tracks
    ndcg_scores = [0 if np.isnan(x) or np.isinf(x) else x for x in ndcg_scores]
    avg_ndcg = np.mean(ndcg_scores)

    # Print the result
    print(f'Average ndcg@{k}: {avg_ndcg:.9f}')

    return avg_ndcg

In [ ]:
calc_ndcg_at_10_fusion(info_df, genres, fusion_bert_musicnn)

# Late Fusion

In [65]:
def get_late_fusion(embedding1, embedding2):
    cos_sim_matrix1 = generate_cos_sim_matrix(embedding1)
    cos_sim_matrix2 = generate_cos_sim_matrix(embedding2)
    
    cos_sim_matrix_df = (cos_sim_matrix1 + cos_sim_matrix2)/2
    
    return cos_sim_matrix_df

In [66]:
cos_sim_matrix_late_fusion = get_late_fusion(bert, musicnn)

(767, 10094)
(49, 10094)


In [ ]:
calc_ndcg_at_10_fusion(info_df, genres, cos_sim_matrix_late_fusion)